### Count Digits

Count the number of specific digits occurring over a range of integers.

See [The xxx example problem](https://xxxx/)

In [310]:
# %load TestHarness
debugging = False
#debugging = True

debugging2 = False

logging = True


def dbg(f, *args):
    if debugging:
        print(('  DBG:' + f).format(*args))

def dbg2(f, *args):
    if debugging2:
        print(('  DBG2:' + f).format(*args))
        
def log(f, *args):
    if logging:
        print((f).format(*args))
        
def log_error(f, *args):
    if logging:
        print(('*** ERROR:' + f).format(*args))       
        
def class_name(instance):
    return type(instance).__name__

#------------------------------------------------------------------------------   
import time
from datetime import timedelta

#------------------------------------------------------------------------------
class TestCase(object):
    def __init__(self, name, method, inputs, expected, catchExceptions=False):
        self.name = name
        self.method = method
        self.inputs = inputs
        self.expected = expected
        self.catchExceptions = catchExceptions
        
    def run(self):
        if self.catchExceptions:
            try:
                return self.method(*self.inputs)
            except Exception as x:
                return x
        else:
                return self.method(*self.inputs)

#------------------------------------------------------------------------------
class TestSet(object):
    def __init__(self, cases):
        self.cases = cases
    
    def run_tests(self, repeat=1):
        count = 0
        errors = 0
        total_time = 0
        for case in self.cases:
            count += 1
            start_time = time.time()
            for iteration in range(repeat):
                dbg2("*** Running '{0}' iteration {1}", case.name, iteration+1)
                result = case.run()
            elapsed_time = time.time() - start_time
            total_time += elapsed_time
            if callable(case.expected):
                if not case.expected(result):
                    errors += 1
                    logError("Test {0} failed. Returned {1}", case.name, result)
            elif result != case.expected:
                errors += 1
                logError('Test {0} failed. Returned "{1}", expected "{2}"', case.name, result, case.expected)
        if errors:
            logError("Tests passed: {0}; Failures: {1}", count-errors, errors)
        else:
            log("All {0} tests passed.", count)
        log("Elapsed test time: {0}", timedelta(seconds=total_time))

        


In [311]:
xStack = []
def push(v):
    global xStack
    xStack.append(v)
def pop():
    global xStack
    return xStack.pop()

In [312]:
def digit_count_slow(n, d):
    ''' Get the number of times digit "d" appears in 0..n inclusive. '''
    def single_count(i, d):
        assert i >= 0
        assert d >=0 and d <= 9
        if i == 0: 
            return 0 if d > 0 else 1
        c = 0
        while i > 0:
            c += i % 10 == d
            i //= 10
        return c
    
    c = 0
    for i in range(n+1):
        c += single_count(i, d)
    return c
        

In [313]:
dc = digit_count_slow

In [314]:
print(dc(0, 0))
print(dc(0, 1))
print(dc(3, 4))
print(dc(10, 0))
print(dc(13, 0))
print(dc(13, 1))
print(dc(13, 2))
print(dc(13, 4))
print(dc(256, 1))
print(dc(256, 2))
print(dc(256, 3))
print(dc(56, 3))

1
0
0
2
2
6
2
1
156
113
56
16


In [315]:
sum([digit_count_slow(n, d) for n in range(1000) for d in range(10)])

1396495

In [316]:
sum([digit_count_str(n, d) for n in range(1000) for d in range(10)])

1396495

In [343]:
def digit_count_str(n, d=0):
    ''' Get the number of times digit "d" appears in 0..n inclusive. '''
    s = []
    d_char = str(d)
    for i in range(n+1): s += str(i)
    return sum([ch == d_char for ch in s])

In [1]:
def power10(n):
    ''' get the scale (1, 10, 100, 1000 ...) and the magnitude (power of 10) '''
    assert n >= 0
    scale = 1
    mag = -1
    while scale <= n: 
        scale *= 10
        mag += 1
    if scale > 1: scale = scale // 10
    return scale, mag

In [ ]:
def zdcount(n, digit, scale=-1, mag=0, zeros=False):
    
    ''' Count the number of digits in the range 0..n. 
    
        Including zero is significantly more challenging since
        leading zeros are only significant in 'interior' cases.
        
        Thus zd(3003) is zd(0..3000) + zd(001,002,003)
        zd(4211) is 4*zd(000..999) + zd(000..211)
        
        The critical insight for this problem is that for any number
        xrrrr, there are two different evaluations of rrrr. For the
        first 9999, the leading zeros do not exist, but from 10000
        to xrrrr, we must count the leading zeros.
        
    '''
    if scale < 0: scale, mag = power10(n)
    if n < 10:
        if digit: return 1 if digit <= n else 0
        # The single digit case is tricky, since leading zeros are
        # are implied when a mag>0.
        if scale <= 1 or not zeros: return 1

    dig = n // scale
    rrr = n %  scale
    r99 = scale-1
    nmag = mag - 1
    nscale = scale // 10

    # Number of times the most significant digit is found.
    cnt = 0
    zzz = digit == 0
    
    if zeros or digit:
        if dig > digit:
            cnt = scale
        elif dig == digit:
            cnt = rrr + 1 # Account for this lone digit.

    if digit:
        if mag:
            cnt += zdcount(r99, digit, nscale, nmag) * dig
    else:
        if zeros:
            if mag:
                if dig: cnt += zdcount(r99, 0, nscale, nmag, zzz) * dig
        else:           
            # First count the values up to 999, without the leading zeros:
            cnt = zdcount(r99, 0, nscale, nmag, zeros=False)
            if dig: cnt += zdcount(r99, 0, nscale, nmag, zzz) * (dig-1)
           
    if (digit and mag) or (zeros and mag) or not zeros:
        cnt += zdcount(rrr, digit, nscale, nmag, zzz)     
    return cnt

In [319]:
dc = digit_count_str
power10(33435)

(10000, 4)

In [320]:
def d_count(n, digit, scale=0, mag=0):
    ''' Count the matching non-zero digits (1..9) in the range 0..n
    '''
    assert digit > 0 and digit < 10   
    if scale == 0:
        scale, mag = power10(n)
    count = 0
    if n < 10:
        count = 1 if digit <= n else 0
        return count        
    first_digit = n // scale
    rem = n % scale

    # Number of times the most significant digit is found.
    if first_digit > digit:
        count += scale
        dbg('{0} n={1} first_digit={2} r={3}, count={4}', X, n, first_digit, rem, count)
    elif first_digit == digit:
        count += rem + 1
        dbg('{0} n={1} first_digit={2} r={3}, r+1={4}', X, n, first_digit, rem, count)
    if scale > 1:
        count += d_count(scale-1, digit, scale // 10, mag-1) * first_digit
        dbg('{0} n={1} 999 RETURN count={2}', X, n, count)
        count += d_count(r, digit, scale // 10, mag-1)
        dbg('{0} n={1} REM RETURN count={2}', X, n, count)
    return count

In [382]:
def zcount(n, scale=0, mag=0):
    if scale == 0:
        scale, mag = power10(n)
    X = '--'*(4-mag)
    dbg('{0} n={1} ENTER scale={2}, mag={3}', X, str(n).zfill(mag+1), scale, mag)
    
    if n < 10:
        cnt = 1
        dbg('{0} n={1} 1RETURN count={2}', X, str(n).zfill(mag+1), cnt)
        return cnt
    
    dig = n // scale
    rem = n % scale
    
    if dig == 0:
        cnt = rem
        cnt += zcount(rem, scale // 10, mag-1) * dig
    else:
        cnt = scale
        cnt += zcount(scale-1, scale // 10, mag-1) * dig
        if rem > 0:
            cnt += zcount(rem, scale // 10, mag-1)
    dbg('{0} n={1} RETURN count={2}', X, str(n).zfill(mag+1), cnt)            
    return cnt

def zerod_count(n, scale=0, mag=0):
    ''' Count the number of zero digits in the range 0..n
        This is distinctly different from d_count as leading zeros are
        always significant.
        
        Thus zd(3003) is zd(0..3000) + zd(001,002,003)
        zd(4211) is 4*zd(000..999) + zd(000..211)
    '''        
    if scale == 0:
        scale, mag = power10(n)
    dig = n // scale
    rem = n % scale
    cnt = zcount(scale-1, scale // 10, mag-1) * dig
    #if rem > 0:
    cnt += zcount(rem, scale // 10, mag-1)
    return cnt

In [383]:
n = 100
print(digit_count_str(n))
push(debugging) ; debugging = True
print(zerod_count(n))
debugging=pop()


12
  DBG:------ n=99 ENTER scale=10, mag=1
  DBG:-------- n=9 ENTER scale=1, mag=0
  DBG:-------- n=9 1RETURN count=1
  DBG:-------- n=9 ENTER scale=1, mag=0
  DBG:-------- n=9 1RETURN count=1
  DBG:------ n=99 RETURN count=20
  DBG:------ n=00 ENTER scale=10, mag=1
  DBG:------ n=00 1RETURN count=1
21


In [347]:
def zz(n, scale):   
    return digit_count_str(n+scale, 0) - digit_count_str(scale-1, 0) 

def zerod_count(n, scale=0, mag=0, zeros=False):
    if scale == 0:
        scale, mag = power10(n)
    dig = n // scale
    rem = n % scale
    return dig * zz(scale-1, scale) + zz(rem, scale)


In [358]:
zz(29, 100)

11

In [359]:
print( zerod_count(129))
print( digit_count_str(129))
print( digit_count_str(99))

29
23
10


In [349]:
print(digit_count_str(101, 0))
push(debugging) ; debugging = True
zerod_count(101)
debugging=pop()

13


In [308]:
def digit_count(n, digit):
    assert n >= 0
    assert digit >=0 and digit <= 9
    scale, mag = power10(n)
    dbg('------------------------------------- {0} in n={1}    SCALE={2}', digit, n, scale)   
    if digit == 0:
        return zerod_count(n, digit)
    else:
        return d_count(n, digit)

In [309]:
r = range(99, 101, 1)
print([digit_count_str(z, 0) for z in r])
print([digit_count(z, 0) for z in r])
print([digit_count_str(z, 0) - digit_count(z, 0) for z in r])

[10, 12]
  DBG:------------------------------------- 0 in n=99    SCALE=10
  DBG:------ n=99 ENTER scale=10, mag=1
  DBG:Z------ n=99 REM 9 RETURN count=10
  DBG:------------------------------------- 0 in n=100    SCALE=100
  DBG:---- n=100 ENTER scale=100, mag=2
  DBG:------ n=99 ENTER scale=10, mag=1
  DBG:Z------ n=99 REM 9 RETURN count=10
  DBG:Z---- n=100 99 RETURN count=10
  DBG:------ n=0 ENTER scale=10, mag=1
  DBG:------ n=0 RETURN count=1
  DBG:Z---- n=100 REM 0 RETURN count=11
[10, 11]
  DBG:------------------------------------- 0 in n=99    SCALE=10
  DBG:------ n=99 ENTER scale=10, mag=1
  DBG:Z------ n=99 REM 9 RETURN count=10
  DBG:------------------------------------- 0 in n=100    SCALE=100
  DBG:---- n=100 ENTER scale=100, mag=2
  DBG:------ n=99 ENTER scale=10, mag=1
  DBG:Z------ n=99 REM 9 RETURN count=10
  DBG:Z---- n=100 99 RETURN count=10
  DBG:------ n=0 ENTER scale=10, mag=1
  DBG:------ n=0 RETURN count=1
  DBG:Z---- n=100 REM 0 RETURN count=11
[0, 1]


print([digit_count_str(z, 0) for z in range(100,1000,100)])
print([digit_count(z, 0) for z in range(100,1000,100)])
print([digit_count_str(z, 0) - digit_count(z, 0) for z in range(100,1000,100)])

In [177]:
print([digit_count_str(z, 0) for z in range(1000,2000,100)])
print([digit_count(z, 0) for z in range(1000,2000,100)])
print([digit_count_str(z, 0) - digit_count(z, 0) for z in range(1000,2000,100)])

[193, 312, 332, 352, 372, 392, 412, 432, 452, 472]
[183, 194, 214, 234, 254, 274, 294, 314, 334, 354]
[10, 118, 118, 118, 118, 118, 118, 118, 118, 118]


In [166]:
print(digit_count_slow(100, 0))
print(digit_count(100, 0))

12
12


In [167]:
print(digit_count(56, 3))

16


In [168]:
print(digit_count_slow(100, 0))

12


In [169]:
print(digit_count_slow(256, 1))

156


In [170]:
digit_count(1, 0)
digit_count(1, 1)
digit_count(1, 2)
digit_count(1, 2)
digit_count(2, 2)

1

In [171]:
digit_count(13, 0)

2

In [120]:
all([digit_count_str(x, d) == digit_count(x, d) for x in range(1000) for d in range(0,10)])

  DBG:------------------------------------- 0 in n=0    SCALE=0
  DBG:-- n=0 RETURN count=1
  DBG:------------------------------------- 1 in n=0    SCALE=0
  DBG:-- n=0 RETURN count=0
  DBG:------------------------------------- 2 in n=0    SCALE=0
  DBG:-- n=0 RETURN count=0
  DBG:------------------------------------- 3 in n=0    SCALE=0
  DBG:-- n=0 RETURN count=0
  DBG:------------------------------------- 4 in n=0    SCALE=0
  DBG:-- n=0 RETURN count=0
  DBG:------------------------------------- 5 in n=0    SCALE=0
  DBG:-- n=0 RETURN count=0
  DBG:------------------------------------- 6 in n=0    SCALE=0
  DBG:-- n=0 RETURN count=0
  DBG:------------------------------------- 7 in n=0    SCALE=0
  DBG:-- n=0 RETURN count=0
  DBG:------------------------------------- 8 in n=0    SCALE=0
  DBG:-- n=0 RETURN count=0
  DBG:------------------------------------- 9 in n=0    SCALE=0
  DBG:-- n=0 RETURN count=0
  DBG:------------------------------------- 0 in n=1    SCALE=1
  DBG:-- n=1 RET

  DBG:-- n=26 999 RETURN count=2
  DBG:---- n=6 RETURN count=1
  DBG:-- n=26 REM RETURN count=3
  DBG:------------------------------------- 5 in n=26    SCALE=10
  DBG:---- n=9 RETURN count=1
  DBG:-- n=26 999 RETURN count=2
  DBG:---- n=6 RETURN count=1
  DBG:-- n=26 REM RETURN count=3
  DBG:------------------------------------- 6 in n=26    SCALE=10
  DBG:---- n=9 RETURN count=1
  DBG:-- n=26 999 RETURN count=2
  DBG:---- n=6 RETURN count=1
  DBG:-- n=26 REM RETURN count=3
  DBG:------------------------------------- 7 in n=26    SCALE=10
  DBG:---- n=9 RETURN count=1
  DBG:-- n=26 999 RETURN count=2
  DBG:---- n=6 RETURN count=0
  DBG:-- n=26 REM RETURN count=2
  DBG:------------------------------------- 8 in n=26    SCALE=10
  DBG:---- n=9 RETURN count=1
  DBG:-- n=26 999 RETURN count=2
  DBG:---- n=6 RETURN count=0
  DBG:-- n=26 REM RETURN count=2
  DBG:------------------------------------- 9 in n=26    SCALE=10
  DBG:---- n=9 RETURN count=1
  DBG:-- n=26 999 RETURN count=2
  DBG:-

  DBG:-- n=59 REM RETURN count=6
  DBG:------------------------------------- 7 in n=59    SCALE=10
  DBG:---- n=9 RETURN count=1
  DBG:-- n=59 999 RETURN count=5
  DBG:---- n=9 RETURN count=1
  DBG:-- n=59 REM RETURN count=6
  DBG:------------------------------------- 8 in n=59    SCALE=10
  DBG:---- n=9 RETURN count=1
  DBG:-- n=59 999 RETURN count=5
  DBG:---- n=9 RETURN count=1
  DBG:-- n=59 REM RETURN count=6
  DBG:------------------------------------- 9 in n=59    SCALE=10
  DBG:---- n=9 RETURN count=1
  DBG:-- n=59 999 RETURN count=5
  DBG:---- n=9 RETURN count=1
  DBG:-- n=59 REM RETURN count=6
  DBG:------------------------------------- 0 in n=60    SCALE=10
  DBG:-- n=60 ZEROS RETURN count=7
  DBG:------------------------------------- 1 in n=60    SCALE=10
  DBG:-- n=60 first_digit=6 r=0, count=10
  DBG:---- n=9 RETURN count=1
  DBG:-- n=60 999 RETURN count=16
  DBG:---- n=0 RETURN count=0
  DBG:-- n=60 REM RETURN count=16
  DBG:------------------------------------- 2 in n=60 

  DBG:---- n=9 RETURN count=1
  DBG:-- n=90 999 RETURN count=19
  DBG:---- n=0 RETURN count=0
  DBG:-- n=90 REM RETURN count=19
  DBG:------------------------------------- 2 in n=90    SCALE=10
  DBG:-- n=90 first_digit=9 r=0, count=10
  DBG:---- n=9 RETURN count=1
  DBG:-- n=90 999 RETURN count=19
  DBG:---- n=0 RETURN count=0
  DBG:-- n=90 REM RETURN count=19
  DBG:------------------------------------- 3 in n=90    SCALE=10
  DBG:-- n=90 first_digit=9 r=0, count=10
  DBG:---- n=9 RETURN count=1
  DBG:-- n=90 999 RETURN count=19
  DBG:---- n=0 RETURN count=0
  DBG:-- n=90 REM RETURN count=19
  DBG:------------------------------------- 4 in n=90    SCALE=10
  DBG:-- n=90 first_digit=9 r=0, count=10
  DBG:---- n=9 RETURN count=1
  DBG:-- n=90 999 RETURN count=19
  DBG:---- n=0 RETURN count=0
  DBG:-- n=90 REM RETURN count=19
  DBG:------------------------------------- 5 in n=90    SCALE=10
  DBG:-- n=90 first_digit=9 r=0, count=10
  DBG:---- n=9 RETURN count=1
  DBG:-- n=90 999 RETURN c

  DBG:------ n=9 RETURN count=1
  DBG:---- n=99 999 RETURN count=19
  DBG:------ n=9 RETURN count=1
  DBG:---- n=99 REM RETURN count=20
  DBG:-- n=113 999 RETURN count=20
  DBG:------ n=9 RETURN count=1
  DBG:---- n=13 999 RETURN count=1
  DBG:------ n=3 RETURN count=0
  DBG:---- n=13 REM RETURN count=1
  DBG:-- n=113 REM RETURN count=21
  DBG:------------------------------------- 5 in n=113    SCALE=100
  DBG:---- n=99 first_digit=9 r=9, count=10
  DBG:------ n=9 RETURN count=1
  DBG:---- n=99 999 RETURN count=19
  DBG:------ n=9 RETURN count=1
  DBG:---- n=99 REM RETURN count=20
  DBG:-- n=113 999 RETURN count=20
  DBG:------ n=9 RETURN count=1
  DBG:---- n=13 999 RETURN count=1
  DBG:------ n=3 RETURN count=0
  DBG:---- n=13 REM RETURN count=1
  DBG:-- n=113 REM RETURN count=21
  DBG:------------------------------------- 6 in n=113    SCALE=100
  DBG:---- n=99 first_digit=9 r=9, count=10
  DBG:------ n=9 RETURN count=1
  DBG:---- n=99 999 RETURN count=19
  DBG:------ n=9 RETURN coun

...

  DBG:---- n=99 first_digit=9 r=9, count=10
  DBG:------ n=9 RETURN count=1
  DBG:---- n=99 999 RETURN count=19
  DBG:------ n=9 RETURN count=1
  DBG:---- n=99 REM RETURN count=20
  DBG:-- n=957 999 RETURN count=280
  DBG:---- n=57 first_digit=5 r=7, count=10
  DBG:------ n=9 RETURN count=1
  DBG:---- n=57 999 RETURN count=15
  DBG:------ n=7 RETURN count=1
  DBG:---- n=57 REM RETURN count=16
  DBG:-- n=957 REM RETURN count=296
  DBG:------------------------------------- 2 in n=957    SCALE=100
  DBG:-- n=957 first_digit=9 r=57, count=100
  DBG:---- n=99 first_digit=9 r=9, count=10
  DBG:------ n=9 RETURN count=1
  DBG:---- n=99 999 RETURN count=19
  DBG:------ n=9 RETURN count=1
  DBG:---- n=99 REM RETURN count=20
  DBG:-- n=957 999 RETURN count=280
  DBG:---- n=57 first_digit=5 r=7, count=10
  DBG:------ n=9 RETURN count=1
  DBG:---- n=57 999 RETURN count=15
  DBG:------ n=7 RETURN count=1
  DBG:---- n=57 REM RETURN count=16
  DBG:-- n=957 REM RETURN count=296
  DBG:-----------------

  DBG:---- n=68 999 RETURN count=16
  DBG:------ n=8 RETURN count=1
  DBG:---- n=68 REM RETURN count=17
  DBG:-- n=968 REM RETURN count=297
  DBG:------------------------------------- 5 in n=968    SCALE=100
  DBG:-- n=968 first_digit=9 r=68, count=100
  DBG:---- n=99 first_digit=9 r=9, count=10
  DBG:------ n=9 RETURN count=1
  DBG:---- n=99 999 RETURN count=19
  DBG:------ n=9 RETURN count=1
  DBG:---- n=99 REM RETURN count=20
  DBG:-- n=968 999 RETURN count=280
  DBG:---- n=68 first_digit=6 r=8, count=10
  DBG:------ n=9 RETURN count=1
  DBG:---- n=68 999 RETURN count=16
  DBG:------ n=8 RETURN count=1
  DBG:---- n=68 REM RETURN count=17
  DBG:-- n=968 REM RETURN count=297
  DBG:------------------------------------- 6 in n=968    SCALE=100
  DBG:-- n=968 first_digit=9 r=68, count=100
  DBG:---- n=99 first_digit=9 r=9, count=10
  DBG:------ n=9 RETURN count=1
  DBG:---- n=99 999 RETURN count=19
  DBG:------ n=9 RETURN count=1
  DBG:---- n=99 REM RETURN count=20
  DBG:-- n=968 999 RET

  DBG:---- n=99 REM RETURN count=20
  DBG:-- n=980 999 RETURN count=280
  DBG:---- n=80 first_digit=8 r=0, count=10
  DBG:------ n=9 RETURN count=1
  DBG:---- n=80 999 RETURN count=18
  DBG:------ n=0 RETURN count=0
  DBG:---- n=80 REM RETURN count=18
  DBG:-- n=980 REM RETURN count=298
  DBG:------------------------------------- 5 in n=980    SCALE=100
  DBG:-- n=980 first_digit=9 r=80, count=100
  DBG:---- n=99 first_digit=9 r=9, count=10
  DBG:------ n=9 RETURN count=1
  DBG:---- n=99 999 RETURN count=19
  DBG:------ n=9 RETURN count=1
  DBG:---- n=99 REM RETURN count=20
  DBG:-- n=980 999 RETURN count=280
  DBG:---- n=80 first_digit=8 r=0, count=10
  DBG:------ n=9 RETURN count=1
  DBG:---- n=80 999 RETURN count=18
  DBG:------ n=0 RETURN count=0
  DBG:---- n=80 REM RETURN count=18
  DBG:-- n=980 REM RETURN count=298
  DBG:------------------------------------- 6 in n=980    SCALE=100
  DBG:-- n=980 first_digit=9 r=80, count=100
  DBG:---- n=99 first_digit=9 r=9, count=10
  DBG:----

  DBG:------ n=9 RETURN count=1
  DBG:---- n=99 REM RETURN count=20
  DBG:-- n=991 999 RETURN count=280
  DBG:---- n=91 first_digit=9 r=1, count=10
  DBG:------ n=9 RETURN count=1
  DBG:---- n=91 999 RETURN count=19
  DBG:------ n=1 RETURN count=0
  DBG:---- n=91 REM RETURN count=19
  DBG:-- n=991 REM RETURN count=299
  DBG:------------------------------------- 4 in n=991    SCALE=100
  DBG:-- n=991 first_digit=9 r=91, count=100
  DBG:---- n=99 first_digit=9 r=9, count=10
  DBG:------ n=9 RETURN count=1
  DBG:---- n=99 999 RETURN count=19
  DBG:------ n=9 RETURN count=1
  DBG:---- n=99 REM RETURN count=20
  DBG:-- n=991 999 RETURN count=280
  DBG:---- n=91 first_digit=9 r=1, count=10
  DBG:------ n=9 RETURN count=1
  DBG:---- n=91 999 RETURN count=19
  DBG:------ n=1 RETURN count=0
  DBG:---- n=91 REM RETURN count=19
  DBG:-- n=991 REM RETURN count=299
  DBG:------------------------------------- 5 in n=991    SCALE=100
  DBG:-- n=991 first_digit=9 r=91, count=100
  DBG:---- n=99 first_

False

In [41]:
[format("n={0} d={1} fast={2} slow={3} ok={4}".format(x, d, 
        digit_count(x, d), digit_count_slow(x, d),
        digit_count_slow(x, d) == digit_count(x, d)))
        for x in range(103) for d in range(3)]

- d=0 n=10 count=2
- d=0 n=10 count=2
--- d=1 first_digit=1 r=0, r+1=1
- d=1 n=10 count=2
--- d=1 first_digit=1 r=0, r+1=1
- d=1 n=10 count=2
- d=2 n=10 count=1
- d=2 n=10 count=1
- d=0 n=11 count=2
- d=0 n=11 count=2
--- d=1 first_digit=1 r=1, r+1=2
- d=1 n=11 count=4
--- d=1 first_digit=1 r=1, r+1=2
- d=1 n=11 count=4
- d=2 n=11 count=1
- d=2 n=11 count=1
- d=0 n=12 count=2
- d=0 n=12 count=2
--- d=1 first_digit=1 r=2, r+1=3
- d=1 n=12 count=5
--- d=1 first_digit=1 r=2, r+1=3
- d=1 n=12 count=5
- d=2 n=12 count=2
- d=2 n=12 count=2
- d=0 n=13 count=2
- d=0 n=13 count=2
--- d=1 first_digit=1 r=3, r+1=4
- d=1 n=13 count=6
--- d=1 first_digit=1 r=3, r+1=4
- d=1 n=13 count=6
- d=2 n=13 count=2
- d=2 n=13 count=2
- d=0 n=14 count=2
- d=0 n=14 count=2
--- d=1 first_digit=1 r=4, r+1=5
- d=1 n=14 count=7
--- d=1 first_digit=1 r=4, r+1=5
- d=1 n=14 count=7
- d=2 n=14 count=2
- d=2 n=14 count=2
- d=0 n=15 count=2
- d=0 n=15 count=2
--- d=1 first_digit=1 r=5, r+1=6
- d=1 n=15 count=8
--- d=1 fi

['n=0 d=0 fast=1 slow=1 ok=True',
 'n=0 d=1 fast=0 slow=0 ok=True',
 'n=0 d=2 fast=0 slow=0 ok=True',
 'n=1 d=0 fast=1 slow=1 ok=True',
 'n=1 d=1 fast=1 slow=1 ok=True',
 'n=1 d=2 fast=0 slow=0 ok=True',
 'n=2 d=0 fast=1 slow=1 ok=True',
 'n=2 d=1 fast=1 slow=1 ok=True',
 'n=2 d=2 fast=1 slow=1 ok=True',
 'n=3 d=0 fast=1 slow=1 ok=True',
 'n=3 d=1 fast=1 slow=1 ok=True',
 'n=3 d=2 fast=1 slow=1 ok=True',
 'n=4 d=0 fast=1 slow=1 ok=True',
 'n=4 d=1 fast=1 slow=1 ok=True',
 'n=4 d=2 fast=1 slow=1 ok=True',
 'n=5 d=0 fast=1 slow=1 ok=True',
 'n=5 d=1 fast=1 slow=1 ok=True',
 'n=5 d=2 fast=1 slow=1 ok=True',
 'n=6 d=0 fast=1 slow=1 ok=True',
 'n=6 d=1 fast=1 slow=1 ok=True',
 'n=6 d=2 fast=1 slow=1 ok=True',
 'n=7 d=0 fast=1 slow=1 ok=True',
 'n=7 d=1 fast=1 slow=1 ok=True',
 'n=7 d=2 fast=1 slow=1 ok=True',
 'n=8 d=0 fast=1 slow=1 ok=True',
 'n=8 d=1 fast=1 slow=1 ok=True',
 'n=8 d=2 fast=1 slow=1 ok=True',
 'n=9 d=0 fast=1 slow=1 ok=True',
 'n=9 d=1 fast=1 slow=1 ok=True',
 'n=9 d=2 fast

In [3]:
simplecompare = lambda s1, s2: matchCount(s1, s2)
c1 = TestCase('one letter 10 times', 
              simplecompare,
              ["x", "aa xxaaxbbxccx xxxxx"],
              { 'x' : 10 })

c2 = TestCase('ABC', 
              simplecompare, 
              ["ABC", "The quick brown fox jumped over the lazy dog. anda one anda two anda bbbb"],
              lambda r : r['a'] == 7 and r['b'] == 5)
tester = TestSet([c1, c2])

In [248]:
#tester.run_tests()